## Explore possible dataset

In [2]:
import pandas as pd
import numpy as np

train_set = pd.read_csv("numerai_training_data.csv")
train_set

feature1  feature2  feature3  feature4  feature5  feature6  feature7  \
0      0.137662  0.445825  0.471079  0.279196  0.275892  0.861967  0.305975   
1      0.651766  0.242053  0.720764  0.784000  0.685828  0.345841  0.038447   
2      0.810204  0.677403  0.538941  0.442458  0.662420  0.208793  0.592084   
3      0.672010  0.534088  0.336534  0.813820  0.331032  0.278800  0.443542   
4      0.763534  0.070120  0.353167  0.440987  0.426678  0.887997  0.747788   
...         ...       ...       ...       ...       ...       ...       ...   
96315  0.530045  0.471722  0.394395  0.408011  0.237166  0.919977  0.542700   
96316  0.753538  0.751962  0.428348  0.440386  0.389391  0.266298  0.173917   
96317  0.682353  0.445825  0.471079  0.419302  0.444300  0.873598  0.257271   
96318  0.326062  0.038255  0.046713  0.970740  0.010984  0.557922  0.045827   
96319  0.317779  0.709651  0.907558  0.240584  0.776481  0.634011  0.124859   

       feature8  feature9  feature10  ...  feature13  feature14  feature15  \
0      0.222414  0.893704   0.475781  ...   0.024044   0.703299   0.128572   
1      0.326108  0.760536   0.741738  ...   0.544590   0.449178   0.547613   
2      0.439066  0.442903   0.404538  ...   0.796002   0.361473   0.395270   
3      0.728365  0.573129   0.603860  ...   0.190886   0.553522   0.403684   
4      0.975318  0.338439   0.406945  ...   0.440494   0.141096   0.613245   
...         ...       ...        ...  ...        ...        ...        ...   
96315  0.602959  0.466467   0.306012  ...   0.116714   0.797982   0.554460   
96316  0.428854  0.253243   0.052556  ...   0.038071   0.705017   0.143411   
96317  0.519911  0.897590   0.923400  ...   0.537472   0.703141   0.589757   
96318  0.125821  0.923315   0.970768  ...   0.196213   0.095928   0.023720   
96319  0.186515  0.297538   0.167587  ...   0.734121   0.671820   0.272240   

       feature16  feature17  feature18  feature19  feature20  feature21  \
0       0.083492   0.639390   0.299443   0.055273   0.000308   0.784610   
1       0.863165   0.832559   0.682060   0.009634   0.829331   0.969233   
2       0.390462   0.086536   0.578854   0.603345   0.265151   0.052699   
3       0.827155   0.102396   0.323720   0.656344   0.704652   0.152971   
4       0.508625   0.315753   0.397510   0.111777   0.473443   0.259582   
...          ...        ...        ...        ...        ...        ...   
96315   0.608047   0.492612   0.780824   0.375182   0.149828   0.459267   
96316   0.648442   0.735134   0.287030   0.562414   0.176136   0.837028   
96317   0.162736   0.266816   0.346567   0.517469   0.608502   0.217501   
96318   0.888410   0.892054   0.026480   0.314385   0.897213   0.763625   
96319   0.237928   0.729145   0.348339   0.863148   0.246363   0.703311   

       target  
0           1  
1           1  
2           1  
3           0  
4           0  
...       ...  
96315       0  
96316       0  
96317       0  
96318       0  
96319       1  

[96320 rows x 22 columns]

This preprocessing function imports and preprocess the Numerai finance dataset

In [1]:
import pandas as pd
import numpy as np
def preprocessing_new():
    # Read input data
    train = pd.read_csv("numerai_training_data.csv")
    #   Drop the ID column
    X = train.drop("target", axis=1)
    y = train["target"]
    return X, y

This other function imports and preprocess the Mercedes dataset

In [12]:
import pandas as pd
import numpy as np
def preprocessing():
    # Read input data
    train = pd.read_csv("train.csv")
    categorical = ["X0", "X1", "X2", "X3", "X4", "X5", "X6", "X8"]

    #   Convert categorical data
    for c in categorical:
        group_by = train.groupby(by=c)["y"].mean().reset_index().rename(columns={"y": "{}_converted".format(c)})
        train = pd.merge(train, group_by, how='inner', on=c)

    train = train.drop(categorical, axis=1)

    #   Drop the ID column
    X = train.drop("ID", axis=1).drop("y", axis=1)
    y = train["y"]
    return X, y

This function creates the Grid search space

In [13]:
import itertools
def get_grid_iterable():
    param_grid = {'learning_rate': [float(v) for v in np.arange(0.01, 0.25, 0.01)],
                  'subsample': [float(v) for v in np.arange(0.5, 1.01, 0.1)],
                  'reg_alpha': [float(v) for v in np.arange(0.01, 0.5, 0.05)],
                  'max_depth': [int(v) for v in np.arange(3, 14, 1)],
                  'gamma': [int(v) for v in np.arange(0, 10, 2)]
                  }
    grid_iter = []
    length = 1
    for k in param_grid:
        grid_iter.append(param_grid[k])
        length *= len(param_grid[k])

    return itertools.product(*grid_iter), list(param_grid.keys()), length-1

grid=get_grid_iterable()
print(grid)

(<itertools.product object at 0x000001C15AC1B9A8>, ['learning_rate', 'subsample', 'reg_alpha', 'max_depth', 'gamma'], 79199)


In [17]:
from sklearn.metrics import r2_score

def xgb_r2_score(preds, dtrain):
    labels = dtrain.get_label()
    return 'r2', r2_score(labels, preds)

[410]	train-rmse:7.47701	valid-rmse:8.06346	train-r2:0.67073	valid-r2:0.51236
[420]	train-rmse:7.41055	valid-rmse:8.04415	train-r2:0.67655	valid-r2:0.51469
[430]	train-rmse:7.35673	valid-rmse:8.02143	train-r2:0.68123	valid-r2:0.51743
[440]	train-rmse:7.30275	valid-rmse:8.00770	train-r2:0.68590	valid-r2:0.51908
[450]	train-rmse:7.25319	valid-rmse:7.99976	train-r2:0.69014	valid-r2:0.52004
[460]	train-rmse:7.21215	valid-rmse:7.98926	train-r2:0.69364	valid-r2:0.52129
[470]	train-rmse:7.16679	valid-rmse:7.99141	train-r2:0.69748	valid-r2:0.52104
[480]	train-rmse:7.13022	valid-rmse:7.99370	train-r2:0.70056	valid-r2:0.52076
[490]	train-rmse:7.09366	valid-rmse:7.99577	train-r2:0.70362	valid-r2:0.52051
[499]	train-rmse:7.06013	valid-rmse:7.99924	train-r2:0.70642	valid-r2:0.52010
[0]	train-rmse:99.65321	valid-rmse:100.91228	train-r2:-60.18624	valid-r2:-64.82658
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 roun

[380]	train-rmse:7.44944	valid-rmse:9.95106	train-r2:0.63299	valid-r2:0.47601
[390]	train-rmse:7.36343	valid-rmse:9.89141	train-r2:0.64141	valid-r2:0.48227
[400]	train-rmse:7.28946	valid-rmse:9.84412	train-r2:0.64858	valid-r2:0.48721
[410]	train-rmse:7.21793	valid-rmse:9.80407	train-r2:0.65544	valid-r2:0.49137
[420]	train-rmse:7.16200	valid-rmse:9.76720	train-r2:0.66076	valid-r2:0.49519
[430]	train-rmse:7.10646	valid-rmse:9.73849	train-r2:0.66600	valid-r2:0.49816
[440]	train-rmse:7.05217	valid-rmse:9.71429	train-r2:0.67109	valid-r2:0.50065
[450]	train-rmse:7.00452	valid-rmse:9.69742	train-r2:0.67552	valid-r2:0.50238
[460]	train-rmse:6.96606	valid-rmse:9.68124	train-r2:0.67907	valid-r2:0.50404
[470]	train-rmse:6.93176	valid-rmse:9.66672	train-r2:0.68222	valid-r2:0.50553
[480]	train-rmse:6.89631	valid-rmse:9.65324	train-r2:0.68547	valid-r2:0.50690
[490]	train-rmse:6.86876	valid-rmse:9.64498	train-r2:0.68797	valid-r2:0.50775
[499]	train-rmse:6.83739	valid-rmse:9.63992	train-r2:0.69082	val

[120]	train-rmse:31.07112	valid-rmse:30.88235	train-r2:-4.68612	valid-r2:-6.15280
[130]	train-rmse:28.34367	valid-rmse:28.13009	train-r2:-3.73167	valid-r2:-4.93469
[140]	train-rmse:25.88453	valid-rmse:25.66208	train-r2:-2.94623	valid-r2:-3.93901
[150]	train-rmse:23.68816	valid-rmse:23.45148	train-r2:-2.30495	valid-r2:-3.12474
[160]	train-rmse:21.72281	valid-rmse:21.48330	train-r2:-1.77929	valid-r2:-2.46145
[170]	train-rmse:19.97116	valid-rmse:19.73149	train-r2:-1.34914	valid-r2:-1.91995
[180]	train-rmse:18.40489	valid-rmse:18.16798	train-r2:-0.99512	valid-r2:-1.47554
[190]	train-rmse:17.01678	valid-rmse:16.78257	train-r2:-0.70552	valid-r2:-1.11238
[200]	train-rmse:15.78121	valid-rmse:15.55500	train-r2:-0.46684	valid-r2:-0.81466
[210]	train-rmse:14.68328	valid-rmse:14.47244	train-r2:-0.26984	valid-r2:-0.57087
[220]	train-rmse:13.71450	valid-rmse:13.51110	train-r2:-0.10780	valid-r2:-0.36911
[230]	train-rmse:12.85164	valid-rmse:12.67628	train-r2:0.02721	valid-r2:-0.20515
[240]	train-rmse:

[90]	train-rmse:41.23538	valid-rmse:41.73337	train-r2:-10.24540	valid-r2:-8.21622
[100]	train-rmse:37.45869	valid-rmse:38.03811	train-r2:-8.27983	valid-r2:-6.65638
[110]	train-rmse:34.04653	valid-rmse:34.70556	train-r2:-6.66621	valid-r2:-5.37358
[120]	train-rmse:30.98068	valid-rmse:31.71218	train-r2:-5.34770	valid-r2:-4.32155
[130]	train-rmse:28.23458	valid-rmse:29.04022	train-r2:-4.27226	valid-r2:-3.46258
[140]	train-rmse:25.75921	valid-rmse:26.64266	train-r2:-3.38833	valid-r2:-2.75613
[150]	train-rmse:23.53962	valid-rmse:24.50318	train-r2:-2.66466	valid-r2:-2.17710
[160]	train-rmse:21.55960	valid-rmse:22.60423	train-r2:-2.07409	valid-r2:-1.70374
[170]	train-rmse:19.77715	valid-rmse:20.90584	train-r2:-1.58679	valid-r2:-1.31271
[180]	train-rmse:18.19705	valid-rmse:19.41014	train-r2:-1.18996	valid-r2:-0.99362
[190]	train-rmse:16.79155	valid-rmse:18.09414	train-r2:-0.86473	valid-r2:-0.73245
[200]	train-rmse:15.53684	valid-rmse:16.93079	train-r2:-0.59647	valid-r2:-0.51684
[210]	train-rmse

[0]	train-rmse:99.86792	valid-rmse:100.25610	train-r2:-57.74272	valid-r2:-74.38369
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:90.41778	valid-rmse:90.73535	train-r2:-47.15150	valid-r2:-60.74601
[20]	train-rmse:81.87937	valid-rmse:82.13304	train-r2:-38.48675	valid-r2:-49.59314
[30]	train-rmse:74.15416	valid-rmse:74.34300	train-r2:-31.38719	valid-r2:-40.45109
[40]	train-rmse:67.17519	valid-rmse:67.30468	train-r2:-25.57787	valid-r2:-32.97398
[50]	train-rmse:60.87748	valid-rmse:60.95026	train-r2:-20.82809	valid-r2:-26.86165
[60]	train-rmse:55.18510	valid-rmse:55.21508	train-r2:-16.93683	valid-r2:-21.86500
[70]	train-rmse:50.05277	valid-rmse:50.03349	train-r2:-13.75566	valid-r2:-17.77490
[80]	train-rmse:45.42960	valid-rmse:45.36933	train-r2:-11.15571	valid-r2:-14.43763
[90]	train-rmse:41.25962	valid-rmse:41.15540	train-r2:-9.02658	valid-r2:-11.70310
[100]	train-rmse:37.50235	vali

...

[300]	train-rmse:8.71038	valid-rmse:11.12009	train-r2:0.49823	valid-r2:0.34566
[310]	train-rmse:8.39788	valid-rmse:10.88323	train-r2:0.53358	valid-r2:0.37324
[320]	train-rmse:8.12914	valid-rmse:10.69256	train-r2:0.56296	valid-r2:0.39501
[330]	train-rmse:7.89638	valid-rmse:10.52688	train-r2:0.58763	valid-r2:0.41361
[340]	train-rmse:7.68133	valid-rmse:10.39317	train-r2:0.60978	valid-r2:0.42841
[350]	train-rmse:7.49152	valid-rmse:10.27176	train-r2:0.62883	valid-r2:0.44169
[360]	train-rmse:7.32977	valid-rmse:10.16425	train-r2:0.64468	valid-r2:0.45332
[370]	train-rmse:7.18794	valid-rmse:10.08413	train-r2:0.65830	valid-r2:0.46190
[380]	train-rmse:7.06572	valid-rmse:10.01183	train-r2:0.66982	valid-r2:0.46959
[390]	train-rmse:6.95854	valid-rmse:9.94797	train-r2:0.67976	valid-r2:0.47633
[400]	train-rmse:6.86524	valid-rmse:9.89854	train-r2:0.68829	valid-r2:0.48152
[410]	train-rmse:6.77519	valid-rmse:9.85778	train-r2:0.69642	valid-r2:0.48579
[420]	train-rmse:6.70563	valid-rmse:9.81922	train-r2:0.

[100]	train-rmse:37.50276	valid-rmse:37.36547	train-r2:-7.28379	valid-r2:-9.47121
[110]	train-rmse:34.11469	valid-rmse:33.95012	train-r2:-5.85465	valid-r2:-7.64447
[120]	train-rmse:31.07153	valid-rmse:30.88036	train-r2:-4.68627	valid-r2:-6.15189
[130]	train-rmse:28.34351	valid-rmse:28.12892	train-r2:-3.73162	valid-r2:-4.93419
[140]	train-rmse:25.88389	valid-rmse:25.66048	train-r2:-2.94604	valid-r2:-3.93839
[150]	train-rmse:23.68571	valid-rmse:23.45307	train-r2:-2.30427	valid-r2:-3.12530
[160]	train-rmse:21.71643	valid-rmse:21.48572	train-r2:-1.77766	valid-r2:-2.46223
[170]	train-rmse:19.96186	valid-rmse:19.73582	train-r2:-1.34695	valid-r2:-1.92124
[180]	train-rmse:18.38895	valid-rmse:18.17874	train-r2:-0.99166	valid-r2:-1.47847
[190]	train-rmse:16.99857	valid-rmse:16.80256	train-r2:-0.70187	valid-r2:-1.11742
[200]	train-rmse:15.75726	valid-rmse:15.59600	train-r2:-0.46239	valid-r2:-0.82424
[210]	train-rmse:14.64983	valid-rmse:14.52679	train-r2:-0.26406	valid-r2:-0.58269
[220]	train-rmse

[70]	train-rmse:50.08530	valid-rmse:50.40442	train-r2:-15.59034	valid-r2:-12.44382
[80]	train-rmse:45.42786	valid-rmse:45.83709	train-r2:-12.64832	valid-r2:-10.11782
[90]	train-rmse:41.23552	valid-rmse:41.73179	train-r2:-10.24546	valid-r2:-8.21552
[100]	train-rmse:37.45888	valid-rmse:38.03669	train-r2:-8.27992	valid-r2:-6.65581
[110]	train-rmse:34.04676	valid-rmse:34.70427	train-r2:-6.66631	valid-r2:-5.37311
[120]	train-rmse:30.98080	valid-rmse:31.71112	train-r2:-5.34775	valid-r2:-4.32119
[130]	train-rmse:28.23492	valid-rmse:29.03871	train-r2:-4.27239	valid-r2:-3.46211
[140]	train-rmse:25.75910	valid-rmse:26.64074	train-r2:-3.38830	valid-r2:-2.75559
[150]	train-rmse:23.53943	valid-rmse:24.50117	train-r2:-2.66460	valid-r2:-2.17658
[160]	train-rmse:21.55995	valid-rmse:22.60515	train-r2:-2.07418	valid-r2:-1.70396
[170]	train-rmse:19.77951	valid-rmse:20.91485	train-r2:-1.58741	valid-r2:-1.31470
[180]	train-rmse:18.19936	valid-rmse:19.42315	train-r2:-1.19052	valid-r2:-0.99630
[190]	train-rm

[0]	train-rmse:99.86792	valid-rmse:100.25610	train-r2:-57.74273	valid-r2:-74.38369
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:90.41783	valid-rmse:90.73541	train-r2:-47.15156	valid-r2:-60.74609
[20]	train-rmse:81.87948	valid-rmse:82.13315	train-r2:-38.48685	valid-r2:-49.59327
[30]	train-rmse:74.15432	valid-rmse:74.34315	train-r2:-31.38733	valid-r2:-40.45125
[40]	train-rmse:67.17539	valid-rmse:67.30487	train-r2:-25.57803	valid-r2:-32.97417
[50]	train-rmse:60.87772	valid-rmse:60.95047	train-r2:-20.82826	valid-r2:-26.86185
[60]	train-rmse:55.18536	valid-rmse:55.21532	train-r2:-16.93701	valid-r2:-21.86521
[70]	train-rmse:50.05307	valid-rmse:50.03377	train-r2:-13.75583	valid-r2:-17.77510
[80]	train-rmse:45.42992	valid-rmse:45.36963	train-r2:-11.15588	valid-r2:-14.43783
[90]	train-rmse:41.26001	valid-rmse:41.15572	train-r2:-9.02677	valid-r2:-11.70329
[100]	train-rmse:37.50276	vali

[480]	train-rmse:6.35273	valid-rmse:8.35694	train-r2:0.75135	valid-r2:0.54855
[490]	train-rmse:6.29817	valid-rmse:8.35112	train-r2:0.75560	valid-r2:0.54918
[499]	train-rmse:6.24352	valid-rmse:8.35243	train-r2:0.75982	valid-r2:0.54904
[0]	train-rmse:100.08448	valid-rmse:99.62860	train-r2:-65.24726	valid-r2:-51.52352
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:90.59788	valid-rmse:90.26929	train-r2:-53.28385	valid-r2:-42.11871
[20]	train-rmse:82.01620	valid-rmse:81.81622	train-r2:-43.48707	valid-r2:-34.42130
[30]	train-rmse:74.26784	valid-rmse:74.18681	train-r2:-35.47843	valid-r2:-28.12320
[40]	train-rmse:67.26782	valid-rmse:67.29356	train-r2:-28.92605	valid-r2:-22.96253
[50]	train-rmse:60.94615	valid-rmse:61.07719	train-r2:-23.56559	valid-r2:-18.73985
[60]	train-rmse:55.23431	valid-rmse:55.46317	train-r2:-19.17681	valid-r2:-15.27778
[70]	train-rmse:50.08530	valid-rmse:50.40442

### Decorator for timing out the functions

In [15]:
from threading import Thread
import functools

def timeout(seconds_before_timeout):
    def deco(func):
        @functools.wraps(func)
        def wrapper(*args, **kwargs):
            res = [Exception('function [%s] timeout [%s seconds] exceeded!' % (func.__name__, seconds_before_timeout))]
            def newFunc():
                try:
                    res[0] = func(*args, **kwargs)
                except Exception as e:
                    res[0] = e
            t = Thread(target=newFunc)
            t.daemon = True
            try:
                t.start()
                t.join(seconds_before_timeout)
            except Exception as e:
                print('error starting thread')
                raise e
            ret = res[0]
            if isinstance(ret, BaseException):
                raise ret
            return ret
        return wrapper
    return deco

In [16]:
import numpy as np
import pandas as pd
import xgboost as xgb
from sklearn.model_selection import KFold  # import KFold
from sklearn.metrics import r2_score
import json
@timeout(3600)
def grid_search(cv_splits, boosting_rounds):
    #   Read input data
    X, y = preprocessing()

    #   Create dataframe to collect the results
    tests_columns = ["test_nr", "cv_mean", "cv_min", "cv_max", "cv_median", "params"]
    test_id = 0
    tests = pd.DataFrame(columns=tests_columns)

    #   Cross validation number of splits
    kf = KFold(n_splits=cv_splits)

    #   Execute until timeout occurs
    while(True):
        #   Get the grid
        grid_iter, keys, length = get_grid_iterable()
        try:    #   For every element of the grid
            for df_grid in grid_iter:
                        #   Prepare a list to collect the scores
                score = []
                params = dict(zip(keys, df_grid))

                        #   The objective function
                params["objective"] = "reg:squarederror"

                        #   For each fold, train XGBoost and spit out the results
                for train_index, test_index in kf.split(X.values):

                            #   Get X train and X test
                    X_train, X_test = X.iloc[train_index], X.iloc[test_index]

                            #   Get y train and y test
                    y_train, y_test = y.iloc[train_index], y.iloc[test_index]

                            #   Convert into DMatrix
                    d_train = xgb.DMatrix(X_train, label=y_train)
                    d_valid = xgb.DMatrix(X_test, label=y_test)
                    d_test = xgb.DMatrix(X_test)
                    watchlist = [(d_train, 'train'), (d_valid, 'valid')]

                            #   Create the classifier using the current grid params. Apply early stopping of 50 rounds
                    clf = xgb.train(params, d_train, boosting_rounds, watchlist, early_stopping_rounds=20,
                                        feval=xgb_r2_score, maximize=True, verbose_eval=10)
                    y_hat = clf.predict(d_test)

                            #   Append Scores on the fold kept out
                    score.append(r2_score(y_test, y_hat))

                        #   Store the result into a dataframe
                score_df = pd.DataFrame(columns=tests_columns, data=[
                    [test_id, np.mean(score), np.min(score), np.max(score), np.median(score),
                        json.dumps(dict(zip(keys, [str(g) for g in df_grid])))]])
                test_id += 1
                tests = pd.concat([tests, score_df])
                tests.to_csv("grid-search.csv", index=False)
                print(tests)
        except RuntimeError:
                    #   When timeout occurs an exception is raised and the main cycle is broken
            pass

    #   Spit out the results
    tests.to_csv("grid-search.csv", index=False)
    print(tests)
import itertools
grid_search(cv_splits=4, boosting_rounds=500)

[0]	train-rmse:99.86792	valid-rmse:100.25610	train-r2:-57.74272	valid-r2:-74.38369
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:90.41778	valid-rmse:90.73535	train-r2:-47.15150	valid-r2:-60.74601
[20]	train-rmse:81.87937	valid-rmse:82.13304	train-r2:-38.48675	valid-r2:-49.59314
[30]	train-rmse:74.15416	valid-rmse:74.34300	train-r2:-31.38719	valid-r2:-40.45109
[40]	train-rmse:67.17519	valid-rmse:67.30468	train-r2:-25.57787	valid-r2:-32.97398
[50]	train-rmse:60.87748	valid-rmse:60.95026	train-r2:-20.82809	valid-r2:-26.86165
[60]	train-rmse:55.18510	valid-rmse:55.21508	train-r2:-16.93683	valid-r2:-21.86500
[70]	train-rmse:50.05277	valid-rmse:50.03349	train-r2:-13.75566	valid-r2:-17.77490
[80]	train-rmse:45.42960	valid-rmse:45.36933	train-r2:-11.15571	valid-r2:-14.43763
[90]	train-rmse:41.25962	valid-rmse:41.15540	train-r2:-9.02658	valid-r2:-11.70310
[100]	train-rmse:37.50218	vali

Exception: function [grid_search] timeout [10 seconds] exceeded!

[220]	train-rmse:13.82174	valid-rmse:13.46016	train-r2:-0.12519	valid-r2:-0.35880
[230]	train-rmse:12.99594	valid-rmse:12.62336	train-r2:0.00524	valid-r2:-0.19510
[240]	train-rmse:12.28034	valid-rmse:11.89903	train-r2:0.11177	valid-r2:-0.06189
[250]	train-rmse:11.65448	valid-rmse:11.26239	train-r2:0.20000	valid-r2:0.04870
[260]	train-rmse:11.11829	valid-rmse:10.71748	train-r2:0.27192	valid-r2:0.13853
[270]	train-rmse:10.65587	valid-rmse:10.24439	train-r2:0.33122	valid-r2:0.21290
[280]	train-rmse:10.25464	valid-rmse:9.83960	train-r2:0.38064	valid-r2:0.27388
[290]	train-rmse:9.91843	valid-rmse:9.49978	train-r2:0.42059	valid-r2:0.32316
[300]	train-rmse:9.63014	valid-rmse:9.21032	train-r2:0.45378	valid-r2:0.36378
[310]	train-rmse:9.38245	valid-rmse:8.95950	train-r2:0.48152	valid-r2:0.39796
[320]	train-rmse:9.17596	valid-rmse:8.75435	train-r2:0.50409	valid-r2:0.42522
[330]	train-rmse:9.00095	valid-rmse:8.58329	train-r2:0.52282	valid-r2:0.44746
[340]	train-rmse:8.84830	valid-rmse:8.44299	tra

[190]	train-rmse:16.79888	valid-rmse:18.05277	train-r2:-0.86636	valid-r2:-0.72454
[200]	train-rmse:15.55307	valid-rmse:16.88246	train-r2:-0.59981	valid-r2:-0.50819
[210]	train-rmse:14.44809	valid-rmse:15.84839	train-r2:-0.38056	valid-r2:-0.32910
[220]	train-rmse:13.47655	valid-rmse:14.94785	train-r2:-0.20114	valid-r2:-0.18234
[230]	train-rmse:12.62087	valid-rmse:14.15950	train-r2:-0.05345	valid-r2:-0.06092
[240]	train-rmse:11.87869	valid-rmse:13.47937	train-r2:0.06681	valid-r2:0.03855
[250]	train-rmse:11.23164	valid-rmse:12.89486	train-r2:0.16570	valid-r2:0.12013
[260]	train-rmse:10.66893	valid-rmse:12.38666	train-r2:0.24721	valid-r2:0.18812
[270]	train-rmse:10.18472	valid-rmse:11.95309	train-r2:0.31399	valid-r2:0.24396
[280]	train-rmse:9.77144	valid-rmse:11.58494	train-r2:0.36853	valid-r2:0.28981
[290]	train-rmse:9.42017	valid-rmse:11.27141	train-r2:0.41312	valid-r2:0.32773
[300]	train-rmse:9.11931	valid-rmse:11.00623	train-r2:0.45000	valid-r2:0.35899
[310]	train-rmse:8.86055	valid-rm

[130]	train-rmse:28.34635	valid-rmse:28.12536	train-r2:-3.73257	valid-r2:-4.93269
[140]	train-rmse:25.89050	valid-rmse:25.65542	train-r2:-2.94806	valid-r2:-3.93644
[150]	train-rmse:23.69961	valid-rmse:23.44475	train-r2:-2.30815	valid-r2:-3.12237
[160]	train-rmse:21.74274	valid-rmse:21.47208	train-r2:-1.78439	valid-r2:-2.45784
[170]	train-rmse:19.99961	valid-rmse:19.71681	train-r2:-1.35584	valid-r2:-1.91561
[180]	train-rmse:18.44020	valid-rmse:18.14333	train-r2:-1.00278	valid-r2:-1.46882
[190]	train-rmse:17.06341	valid-rmse:16.74913	train-r2:-0.71488	valid-r2:-1.10397
[200]	train-rmse:15.84648	valid-rmse:15.51294	train-r2:-0.47900	valid-r2:-0.80486
[210]	train-rmse:14.76769	valid-rmse:14.42254	train-r2:-0.28448	valid-r2:-0.56005
[220]	train-rmse:13.82170	valid-rmse:13.46005	train-r2:-0.12519	valid-r2:-0.35878
[230]	train-rmse:12.99592	valid-rmse:12.62326	train-r2:0.00524	valid-r2:-0.19509
[240]	train-rmse:12.28027	valid-rmse:11.89858	train-r2:0.11178	valid-r2:-0.06181
[250]	train-rmse:1

...

[90]	train-rmse:41.25962	valid-rmse:41.15540	train-r2:-9.02658	valid-r2:-11.70310
[100]	train-rmse:37.50229	valid-rmse:37.36527	train-r2:-7.28357	valid-r2:-9.47110
[110]	train-rmse:34.11436	valid-rmse:33.94946	train-r2:-5.85451	valid-r2:-7.64414
[120]	train-rmse:31.07304	valid-rmse:30.88178	train-r2:-4.68682	valid-r2:-6.15254
[130]	train-rmse:28.34638	valid-rmse:28.12839	train-r2:-3.73258	valid-r2:-4.93397
[140]	train-rmse:25.88745	valid-rmse:25.65892	train-r2:-2.94712	valid-r2:-3.93779
[150]	train-rmse:23.69296	valid-rmse:23.44891	train-r2:-2.30629	valid-r2:-3.12384
[160]	train-rmse:21.72992	valid-rmse:21.48054	train-r2:-1.78111	valid-r2:-2.46056
[170]	train-rmse:19.98015	valid-rmse:19.72574	train-r2:-1.35126	valid-r2:-1.91825
[180]	train-rmse:18.41506	valid-rmse:18.16010	train-r2:-0.99733	valid-r2:-1.47339
[190]	train-rmse:17.02871	valid-rmse:16.76594	train-r2:-0.70791	valid-r2:-1.10820
[200]	train-rmse:15.79823	valid-rmse:15.53388	train-r2:-0.47001	valid-r2:-0.80974
[210]	train-rmse

[60]	train-rmse:55.23403	valid-rmse:55.46287	train-r2:-19.17662	valid-r2:-15.27760
[70]	train-rmse:50.08500	valid-rmse:50.40407	train-r2:-15.59014	valid-r2:-12.44364
[80]	train-rmse:45.42753	valid-rmse:45.83672	train-r2:-12.64812	valid-r2:-10.11764
[90]	train-rmse:41.23515	valid-rmse:41.73140	train-r2:-10.24527	valid-r2:-8.21534
[100]	train-rmse:37.45850	valid-rmse:38.03627	train-r2:-8.27973	valid-r2:-6.65564
[110]	train-rmse:34.04637	valid-rmse:34.70385	train-r2:-6.66614	valid-r2:-5.37296
[120]	train-rmse:30.98045	valid-rmse:31.71070	train-r2:-5.34761	valid-r2:-4.32105
[130]	train-rmse:28.23423	valid-rmse:29.03889	train-r2:-4.27213	valid-r2:-3.46217
[140]	train-rmse:25.75896	valid-rmse:26.63943	train-r2:-3.38825	valid-r2:-2.75522
[150]	train-rmse:23.53957	valid-rmse:24.50105	train-r2:-2.66465	valid-r2:-2.17655
[160]	train-rmse:21.55917	valid-rmse:22.60018	train-r2:-2.07396	valid-r2:-1.70277
[170]	train-rmse:19.77752	valid-rmse:20.89680	train-r2:-1.58689	valid-r2:-1.31071
[180]	train-r

[0]	train-rmse:99.86792	valid-rmse:100.25610	train-r2:-57.74272	valid-r2:-74.38369
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:90.41778	valid-rmse:90.73535	train-r2:-47.15150	valid-r2:-60.74601
[20]	train-rmse:81.87937	valid-rmse:82.13304	train-r2:-38.48675	valid-r2:-49.59314
[30]	train-rmse:74.15416	valid-rmse:74.34300	train-r2:-31.38719	valid-r2:-40.45109
[40]	train-rmse:67.17519	valid-rmse:67.30468	train-r2:-25.57787	valid-r2:-32.97398
[50]	train-rmse:60.87748	valid-rmse:60.95026	train-r2:-20.82809	valid-r2:-26.86165
[60]	train-rmse:55.18510	valid-rmse:55.21508	train-r2:-16.93683	valid-r2:-21.86500
[70]	train-rmse:50.05277	valid-rmse:50.03349	train-r2:-13.75566	valid-r2:-17.77490
[80]	train-rmse:45.42960	valid-rmse:45.36933	train-r2:-11.15571	valid-r2:-14.43763
[90]	train-rmse:41.25962	valid-rmse:41.15540	train-r2:-9.02658	valid-r2:-11.70310
[100]	train-rmse:37.50229	vali

[480]	train-rmse:7.51748	valid-rmse:8.19730	train-r2:0.65181	valid-r2:0.56563
[490]	train-rmse:7.48896	valid-rmse:8.19365	train-r2:0.65445	valid-r2:0.56602
[499]	train-rmse:7.46131	valid-rmse:8.18817	train-r2:0.65699	valid-r2:0.56660
[0]	train-rmse:100.08447	valid-rmse:99.62860	train-r2:-65.24726	valid-r2:-51.52351
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:90.59783	valid-rmse:90.26922	train-r2:-53.28378	valid-r2:-42.11865
[20]	train-rmse:82.01609	valid-rmse:81.81609	train-r2:-43.48695	valid-r2:-34.42119
[30]	train-rmse:74.26769	valid-rmse:74.18663	train-r2:-35.47828	valid-r2:-28.12306
[40]	train-rmse:67.26764	valid-rmse:67.29334	train-r2:-28.92588	valid-r2:-22.96237
[50]	train-rmse:60.94591	valid-rmse:61.07693	train-r2:-23.56540	valid-r2:-18.73968
[60]	train-rmse:55.23403	valid-rmse:55.46287	train-r2:-19.17662	valid-r2:-15.27760
[70]	train-rmse:50.08500	valid-rmse:50.40407

[450]	train-rmse:7.57255	valid-rmse:7.82751	train-r2:0.64019	valid-r2:0.62562
[460]	train-rmse:7.53379	valid-rmse:7.82438	train-r2:0.64386	valid-r2:0.62592
[470]	train-rmse:7.49669	valid-rmse:7.82195	train-r2:0.64736	valid-r2:0.62615
[480]	train-rmse:7.46191	valid-rmse:7.82076	train-r2:0.65063	valid-r2:0.62626
[490]	train-rmse:7.43041	valid-rmse:7.82785	train-r2:0.65357	valid-r2:0.62559
[499]	train-rmse:7.40306	valid-rmse:7.83089	train-r2:0.65612	valid-r2:0.62530
  test_nr   cv_mean    cv_min    cv_max  cv_median  \
0       0  0.564294  0.511647  0.630370   0.557580   
0       1  0.564255  0.511696  0.630383   0.557470   
0       2  0.564144  0.511467  0.630436   0.557336   
0       3  0.564192  0.511466  0.630425   0.557439   
0       4  0.564348  0.511624  0.630601   0.557584   
0       5  0.561067  0.511557  0.628682   0.552015   
0       6  0.561103  0.511505  0.628865   0.552021   
0       7  0.560945  0.511381  0.628673   0.551864   
0       8  0.560997  0.511274  0.628960   0.55

This function creates the random search space

In [4]:
# Imports
import random
import math

def generate_random_configuration():
    params = {'learning_rate': random.uniform(0.01, 0.25),
              'subsample': random.uniform(0.5, 1.0),
              'reg_alpha': random.uniform(0.01, 0.5),
              'max_depth': math.floor(random.uniform(3, 15)),
              'gamma': math.floor(random.uniform(0, 10))
              }
    return params

In [5]:
# Imports
import numpy as np
import pandas as pd
import xgboost as xgb
from sklearn.model_selection import KFold  # import KFold
from sklearn.metrics import r2_score
import json

@timeout(8)
def random_search(cv_splits, boosting_rounds):
    #   Read input data
    X, y = preprocessing()

    #   Create dataframe to collect the results
    tests_columns = ["test_nr", "cv_mean", "cv_min", "cv_max", "cv_median", "params"]
    test_id = 0
    tests = pd.DataFrame(columns=tests_columns)

    #   Cross validation number of splits
    kf = KFold(n_splits=cv_splits)

    #   Execute until timeout occurs
    while True:
        try:
            while True:
                #   Prepare a list to collect the scores
                score = []
                
                #   Obtain a random set of params
                params = generate_random_configuration()

                #   The objective function
                params["objective"] = "reg:squarederror"

                #   For each fold, train XGBoost and spit out the results
                for train_index, test_index in kf.split(X.values):
                    #   Get X train and X test
                    X_train, X_test = X.iloc[train_index], X.iloc[test_index]

                    #   Get y train and y test
                    y_train, y_test = y.iloc[train_index], y.iloc[test_index]

                    #   Convert into DMatrix
                    d_train = xgb.DMatrix(X_train, label=y_train)
                    d_valid = xgb.DMatrix(X_test, label=y_test)
                    watchlist = [(d_train, 'train'), (d_valid, 'valid')]

                    #   Create the classifier using the current grid params. Apply early stopping of 50 rounds
                    clf = xgb.train(params, d_train, boosting_rounds, watchlist, early_stopping_rounds=50,
                                    feval=xgb_r2_score, maximize=True, verbose_eval=10)
                    y_hat = clf.predict(d_valid)

                    #   Append Scores on the fold kept out
                    score.append(r2_score(y_test, y_hat))

                #   Store the result into a dataframe
                score_df = pd.DataFrame(columns=tests_columns, data=[
                    [test_id, np.mean(score), np.min(score), np.max(score), np.median(score),
                     json.dumps(dict(zip(params.keys(), [str(g) for g in params])))]])
                test_id += 1
                tests = pd.concat([tests, score_df])
                tests.to_csv("random-search.csv", index=False)
                print(tests)
        except RuntimeError:
            #   When timeout occurs an exception is raised and the main cycle is broken
            pass

    #   Spit out the results
    tests.to_csv("random-search.csv", index=False)
    print(tests)

           
import itertools
random_search(cv_splits=4, boosting_rounds=500)

[0]	train-rmse:83.14699	valid-rmse:83.40567	train-r2:-39.71883	valid-r2:-51.17314
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:14.47515	valid-rmse:14.13647	train-r2:-0.23409	valid-r2:-0.49878
[20]	train-rmse:8.35220	valid-rmse:7.96935	train-r2:0.58913	valid-r2:0.52368
[30]	train-rmse:8.00316	valid-rmse:7.85285	train-r2:0.62275	valid-r2:0.53750
[40]	train-rmse:7.87534	valid-rmse:7.89713	train-r2:0.63471	valid-r2:0.53227
[50]	train-rmse:7.79780	valid-rmse:7.91528	train-r2:0.64187	valid-r2:0.53012
[60]	train-rmse:7.66461	valid-rmse:8.00404	train-r2:0.65399	valid-r2:0.51952
[70]	train-rmse:7.59792	valid-rmse:8.03758	train-r2:0.65999	valid-r2:0.51548
Stopping. Best iteration:
[27]	train-rmse:8.06863	valid-rmse:7.83219	train-r2:0.61656	valid-r2:0.53993

[0]	train-rmse:82.96756	valid-rmse:84.04481	train-r2:-41.41190	valid-r2:-44.65992
Multiple eval metrics have been passed: 'valid-r

TimeoutError: 

[50]	train-rmse:7.21641	valid-rmse:9.57061	train-r2:0.65559	valid-r2:0.51531
[60]	train-rmse:7.12601	valid-rmse:9.60073	train-r2:0.66416	valid-r2:0.51225
[70]	train-rmse:7.05641	valid-rmse:9.63036	train-r2:0.67069	valid-r2:0.50924
[80]	train-rmse:6.99892	valid-rmse:9.62754	train-r2:0.67604	valid-r2:0.50953
Stopping. Best iteration:
[33]	train-rmse:7.37875	valid-rmse:9.54780	train-r2:0.63992	valid-r2:0.51762

[0]	train-rmse:83.49482	valid-rmse:82.35965	train-r2:-42.74289	valid-r2:-40.44719
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:14.49827	valid-rmse:13.50033	train-r2:-0.31893	valid-r2:-0.11367
[20]	train-rmse:8.37409	valid-rmse:7.80467	train-r2:0.55999	valid-r2:0.62780
[30]	train-rmse:8.09030	valid-rmse:7.83124	train-r2:0.58931	valid-r2:0.62526
[40]	train-rmse:7.93119	valid-rmse:7.92492	train-r2:0.60530	valid-r2:0.61624
[50]	train-rmse:7.84561	valid-rmse:7.90903	train-r2:0

[90]	train-rmse:6.37868	valid-rmse:9.66459	train-r2:0.73091	valid-r2:0.50574
[100]	train-rmse:6.21786	valid-rmse:9.68346	train-r2:0.74431	valid-r2:0.50381
[110]	train-rmse:6.06741	valid-rmse:9.69364	train-r2:0.75653	valid-r2:0.50277
[120]	train-rmse:5.92365	valid-rmse:9.70750	train-r2:0.76793	valid-r2:0.50135
Stopping. Best iteration:
[76]	train-rmse:6.61866	valid-rmse:9.65291	train-r2:0.71028	valid-r2:0.50694

[0]	train-rmse:93.19646	valid-rmse:92.02457	train-r2:-53.49885	valid-r2:-50.74564
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:41.01833	valid-rmse:40.01123	train-r2:-9.55709	valid-r2:-8.78205
[20]	train-rmse:19.30369	valid-rmse:18.32993	train-r2:-1.33813	valid-r2:-1.05299
[30]	train-rmse:10.97343	valid-rmse:10.35864	train-r2:0.24443	valid-r2:0.34435
[40]	train-rmse:8.21243	valid-rmse:8.21280	train-r2:0.57681	valid-r2:0.58786
[50]	train-rmse:7.36172	valid-rmse:7.85337	t

[0]	train-rmse:84.05270	valid-rmse:84.31814	train-r2:-40.61075	valid-r2:-52.32094
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:15.60433	valid-rmse:15.55412	train-r2:-0.43414	valid-r2:-0.81446
[20]	train-rmse:6.36490	valid-rmse:8.49750	train-r2:0.76139	valid-r2:0.45845
[30]	train-rmse:4.62741	valid-rmse:8.63642	train-r2:0.87388	valid-r2:0.44060
[40]	train-rmse:3.89171	valid-rmse:8.83480	train-r2:0.91080	valid-r2:0.41460
[50]	train-rmse:3.35060	valid-rmse:8.94898	train-r2:0.93388	valid-r2:0.39937
[60]	train-rmse:3.05618	valid-rmse:9.05305	train-r2:0.94499	valid-r2:0.38532
[70]	train-rmse:2.82791	valid-rmse:9.07658	train-r2:0.95290	valid-r2:0.38212
Stopping. Best iteration:
[23]	train-rmse:5.59164	valid-rmse:8.47225	train-r2:0.81585	valid-r2:0.46166

[0]	train-rmse:83.87657	valid-rmse:84.96435	train-r2:-42.34634	valid-r2:-45.66452
Multiple eval metrics have been passed: 'valid-r

...

[100]	train-rmse:5.39431	valid-rmse:8.64869	train-r2:0.82072	valid-r2:0.51648
[110]	train-rmse:4.85932	valid-rmse:8.50204	train-r2:0.85451	valid-r2:0.53274
[120]	train-rmse:4.48575	valid-rmse:8.44373	train-r2:0.87602	valid-r2:0.53913
[130]	train-rmse:4.17161	valid-rmse:8.41418	train-r2:0.89278	valid-r2:0.54235
[140]	train-rmse:3.91828	valid-rmse:8.40794	train-r2:0.90541	valid-r2:0.54302
[150]	train-rmse:3.75407	valid-rmse:8.41442	train-r2:0.91317	valid-r2:0.54232
[160]	train-rmse:3.55970	valid-rmse:8.42160	train-r2:0.92193	valid-r2:0.54154
[170]	train-rmse:3.41759	valid-rmse:8.44730	train-r2:0.92804	valid-r2:0.53874
[180]	train-rmse:3.29562	valid-rmse:8.46093	train-r2:0.93308	valid-r2:0.53725
Stopping. Best iteration:
[135]	train-rmse:4.04068	valid-rmse:8.40163	train-r2:0.89940	valid-r2:0.54371

[0]	train-rmse:97.15964	valid-rmse:96.74573	train-r2:-61.43189	valid-r2:-48.52784
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 

[0]	train-rmse:87.62905	valid-rmse:86.47836	train-r2:-47.18196	valid-r2:-44.69629
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:21.92668	valid-rmse:20.93233	train-r2:-2.01671	valid-r2:-1.67733
[20]	train-rmse:9.11954	valid-rmse:8.79046	train-r2:0.47816	valid-r2:0.52784
[30]	train-rmse:7.32291	valid-rmse:7.96967	train-r2:0.66352	valid-r2:0.61190
[40]	train-rmse:6.86113	valid-rmse:8.09724	train-r2:0.70462	valid-r2:0.59937
[50]	train-rmse:6.48938	valid-rmse:8.22206	train-r2:0.73576	valid-r2:0.58693
[60]	train-rmse:6.17941	valid-rmse:8.28754	train-r2:0.76040	valid-r2:0.58032
[70]	train-rmse:5.95040	valid-rmse:8.31844	train-r2:0.77783	valid-r2:0.57719
[80]	train-rmse:5.73027	valid-rmse:8.36543	train-r2:0.79397	valid-r2:0.57239
Stopping. Best iteration:
[31]	train-rmse:7.24066	valid-rmse:7.96454	train-r2:0.67104	valid-r2:0.61240

   test_nr   cv_mean    cv_min    cv_max  cv_median  

[0]	train-rmse:87.02318	valid-rmse:87.33775	train-r2:-43.60385	valid-r2:-56.20842
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:21.32569	valid-rmse:21.02690	train-r2:-1.67860	valid-r2:-2.31594
[20]	train-rmse:9.41075	valid-rmse:8.95398	train-r2:0.47838	valid-r2:0.39870
[30]	train-rmse:8.16779	valid-rmse:7.85607	train-r2:0.60707	valid-r2:0.53712
[40]	train-rmse:8.00331	valid-rmse:7.82396	train-r2:0.62274	valid-r2:0.54090
[50]	train-rmse:7.89782	valid-rmse:7.87647	train-r2:0.63262	valid-r2:0.53472
[60]	train-rmse:7.83107	valid-rmse:7.90504	train-r2:0.63880	valid-r2:0.53133
[70]	train-rmse:7.74266	valid-rmse:7.94189	train-r2:0.64691	valid-r2:0.52695
[80]	train-rmse:7.68225	valid-rmse:7.95548	train-r2:0.65240	valid-r2:0.52533
Stopping. Best iteration:
[38]	train-rmse:8.02891	valid-rmse:7.81260	train-r2:0.62032	valid-r2:0.54223

[0]	train-rmse:86.84171	valid-rmse:87.96180	train-r2:

[100]	train-rmse:7.09049	valid-rmse:9.62287	train-r2:0.66750	valid-r2:0.51000
Stopping. Best iteration:
[55]	train-rmse:7.32965	valid-rmse:9.57615	train-r2:0.64470	valid-r2:0.51475

[0]	train-rmse:88.76400	valid-rmse:87.61317	train-r2:-48.43815	valid-r2:-45.90345
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:24.80151	valid-rmse:23.79842	train-r2:-2.85962	valid-r2:-2.46069
[20]	train-rmse:10.38722	valid-rmse:9.48836	train-r2:0.32300	valid-r2:0.44989
[30]	train-rmse:8.37880	valid-rmse:7.83188	train-r2:0.55949	valid-r2:0.62520
[40]	train-rmse:8.12810	valid-rmse:7.83603	train-r2:0.58546	valid-r2:0.62480
[50]	train-rmse:7.98983	valid-rmse:7.90140	train-r2:0.59944	valid-r2:0.61852
[60]	train-rmse:7.90199	valid-rmse:7.96047	train-r2:0.60820	valid-r2:0.61279
[70]	train-rmse:7.80587	valid-rmse:7.96743	train-r2:0.61768	valid-r2:0.61211
[80]	train-rmse:7.71966	valid-rmse:7.97749	train-r2

[30]	train-rmse:7.84892	valid-rmse:8.14832	train-r2:0.62043	valid-r2:0.57081
[40]	train-rmse:7.69302	valid-rmse:8.36431	train-r2:0.63536	valid-r2:0.54775
[50]	train-rmse:7.58359	valid-rmse:8.48094	train-r2:0.64566	valid-r2:0.53505
[60]	train-rmse:7.52276	valid-rmse:8.51859	train-r2:0.65132	valid-r2:0.53092
Stopping. Best iteration:
[19]	train-rmse:8.06058	valid-rmse:8.04986	train-r2:0.59968	valid-r2:0.58112

[0]	train-rmse:76.07479	valid-rmse:75.96633	train-r2:-37.27508	valid-r2:-29.53711
Multiple eval metrics have been passed: 'valid-r2' will be used for early stopping.

Will train until valid-r2 hasn't improved in 50 rounds.
[10]	train-rmse:8.81864	valid-rmse:10.70199	train-r2:0.48568	valid-r2:0.39394
[20]	train-rmse:7.49392	valid-rmse:9.59613	train-r2:0.62859	valid-r2:0.51272
[30]	train-rmse:7.36068	valid-rmse:9.61018	train-r2:0.64168	valid-r2:0.51129
[40]	train-rmse:7.24313	valid-rmse:9.64409	train-r2:0.65303	valid-r2:0.50784
[50]	train-rmse:7.14270	valid-rmse:9.68901	train-r2:0.66